# Introduction à Python et application pour la data science (2. lire et manipuler des données)
Formations doctorales transversales, cours de Jean-Jil Duchamps et Camelia Goga.

Dans ce notebook, on va voir comment utiliser le paquet **Pandas** pour lire, modifier, structurer, et écrire des données.
On trouvera beaucoup plus d'informations dans le [*user
guide*](https://pandas.pydata.org/docs/user_guide/index.html) officiel
et la documentation (utiliser l'outil recherche). Je vous donne quelques
pistes très rapides pour bien démarrer avec Pandas.

Tout d'abord, pour importer Pandas et Seaborn, on rappelle les alias standards:

In [ ]:
import pandas as pd
import seaborn as sns
# Actuellement, l'utilisation de Seaborn avec Pandas (sur mon ordinateur) produit de nombreux "FutureWarning". Les lignes suivantes les désactivent.
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

Note: Pandas est construit par-dessus Numpy, et Seaborn par-dessus
Matplotlib, donc on pourra importer ces deux autres librairies si besoin
(Numpy en particulier pourra être très utile).

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

## Lecture de données et opérations basiques

### Lire et écrire des données

Lire des données au format CSV avec `df = pd.read_csv(nom_fichier)`.

La variable `nom_fichier` est une chaîne de caractère, contenant soit le
nom d'un fichier sur votre ordinateur, soit une URL vers un fichier en
ligne. Généralement, il vaut mieux sauvegarder le fichier sur votre
ordinateur pour le charger localement, sinon le script va re-télécharger
le fichier en boucle, ce qui serait du gâchis.

On va travailler avec le fichier d'exemple `rec99.csv`, qui contient les données du recensement de
la population des communes de moins de 10000 habitants en Haute-Garonne, en 1999.
La description des variables présentes est trouvable [ici](https://search.r-project.org/CRAN/refmans/sampling/html/rec99.html).

In [ ]:
df = pd.read_csv('rec99.csv', index_col=0)
df

In [ ]:
# Donne quelques propriétés statistiques des colonnes numériques.
# ATTENTION: ici, considérer CODE_N ou BVQ_N comme des colonnes numériques n'a pas de sens (on y reviendra).
df.describe()

Le nom CSV signifie *comma-separated values*, soit “valeurs séparées par
des virgules”: des virgules séparent les colonnes du tableau. *Mais
attention*, parfois le caractère de séparation peut être le
point-virgule (c'est le cas quand on veut mettre des chaînes de
caractères avec des virgules dans les données), auquel cas on aura
peut-être besoin de préciser `df = pd.read_csv(nom_fichier, sep=';')`.

<div class="alert alert-info">
Remarquez ci-dessus que l'on a précisé un argument optionnel <code>index_col=0</code>. Essayer de voir ce qui change quand on l'enlève, ou que l'on modifie la valeur de cet argument.
</div>

La fonction `pd.read_csv` renvoie un objet `DataFrame`: un **tableau**
contenant plusieurs **colonnes** (objets `Series`). Les colonnes ont un
nom, récupéré dans la première ligne du fichier. Une première colonne
est mise à part et appelée l'*index* (objet `Index`): c'est la liste qui
identifie les lignes par des étiquettes (numéros ou chaînes de
caractères). Par défaut avec la fonction `pd.read_csv`, l'index n'a pas
de nom et l'étiquette d'une ligne est son numéro: 0 pour la première, 1
pour la seconde, etc.

#### Changer l'index d'un tableau existant.

- `df = df.reset_index()`. La colonne utilisée pour l'index redeviendra une
colonne “normale”.
- `df.set_index('nom_de_la_colonne')`. **Attention**, l'index existant
sera supprimé.

#### Enregistrer dans un fichier.

- `df.to_csv('mon_fichier.csv')`. Pour ignorer l'index, si celui-ci n'a pas d'intérêt, on rajoute l'argument optionnel `index=False`.

### Afficher un tableau

Pour les grands tableaux, il peut être intéressant d'afficher
seulement les **premières lignes** du tableau avec `df.head()` ou
les **dernières lignes** avec `df.tail()`.

In [ ]:
df.tail()

In [ ]:
# Liste des colonnes.
df.columns  # Attention, columns est un attribut.

In [ ]:
# Types des données.
df.dtypes

Ici, on voit que l'on a plusieurs types de données, et **chaque colonne a un type précis**.
Quelques types importants:
- Numériques (`int64` pour les entiers, `float64` pour les décimaux, etc.)
- Chaîne de caractères (`object` -- en fait ce type peut contenir toute sorte de choses)
- Logique (`bool`)
- Catégoriel (`category`)

Ce dernier est souvent interchangeable avec `object`, mais il est plus *efficace en mémoire*.
De plus, il faut parfois faire attention à la façon dont Pandas interprète ce qu'il lit -- on reviendra là-dessus.

-   On peut, si nécessaire, récupérer la matrice de toutes les valeurs
    du tableau (sans les noms des colonnes et de l'index) avec
    `df.values`. Note: ceci renvoie un array Numpy.
-   Comme les arrays Numpy, `df.shape` renvoie les **dimensions**,
    c'est-à-dire le tuple (nb de lignes, nb de colonnes) du tableau
    (l'index n'est pas compris dans les colonnes).
-   Accès à une colonne du tableau grâce à `df["nom_colonne"]` ou `df.nom_colonne` si celui-ci n'a pas d'espaces, ou autre surprise.
    Le type d'une seule colonne est `Series`. Dans une
    série, *l'index est conservé*. C'est très important car Pandas
    “aligne” et manipule les différentes séries en se basant sur leurs
    index (on en parlera plus tard).

In [ ]:
df['COMMUNE']

-   Les opérations Numpy s'appliquent généralement sur les séries Pandas
    de type numérique:
    

In [ ]:
s = df['POPSDC99']  # Population des communes.
print(s.mean())
print(s.sum())
print(s.min())
print(s.max())

-   On peut connaître l'ensemble des **valeurs prises par une colonne
    (sans répétitions)** en utilisant `df['col'].unique()`, où `col`
    est le nom de la colonne.
-   Accès à plusieurs colonnes du tableau en même temps grâce à
    `df[liste]`, avec  
    `liste = ['col1', 'col2', ...]`. Cette fois, le type obtenu est
    bien un `DataFrame`.

### Modifications basiques

De la même manière que Numpy, **les opérations dans un dataframe se font
de manière vectorielle**, le long des colonnes. On n'a donc **pas besoin
de boucle** `for` pour créer une série à partir de plusieurs séries
existantes.

**Exercice:** rajouter une colonne `densite` pour la densité de population (population / surface) dans le jeu de données `df`.

In [ ]:
# à compléter
# df['densite'] = 

Pour **supprimer une colonne**, trois méthodes:
```python
df = df.drop(columns='densite')
del df['densite']
df.pop('densite')
```
Notons que la première méthode permet de supprimer plusieurs colonnes en
fournissant une liste de noms.

Pour **renommer une colonne** (pratique de faire ça dès le démarrage quand les colonnes ont des noms trop complexes):

In [ ]:
df = df.rename(columns={'CODE_N': 'code', 'POPSDC99': 'pop'})
df.columns  # Le nom des colonnes a changé.

Si votre tableau a peu de colonnes, vous pouvez **les renommer toutes
d'un coup** en exécutant:

In [ ]:
df.columns = ['code', 'commune', 'BVQ_N', 'pop', 'LOG', 'LOGVAC', 'STRATLOG', 'surface', 'lat', 'lon']

**Le cas des dates**: si l'on importe un fichier CSV qui contient des
dates, celles-ci seront interprétés comme du texte par défaut, par
exemple: `'2022-11-22'` au lieu de la date “22 novembre 2022”. Si l'on
a une colonne `date` de type `object` (type des chaînes de caractères
dans un tableau Pandas), on peut les changer en objets de type
`datetime` en utilisant: `df['date'] =
pd.to_datetime(df['date'])`.

Cette transformation est intéressante pour pouvoir trier nos données,
tracer nos données en fonction du temps, faire des opérations sur des
fenêtres roulantes, etc.

<div class="alert alert-info">
<b>Attention à l'interprétation de Pandas</b> car il existe de nombreux formats de dates: allez voir dans la doc pour pouvoir adapter la lecture de vos dates correctement.
</div>

Pour **trier un tableau**, on utilise la méthode `df.sort_values`. Par
exemple, pour trier les villes par nombre décroissant d'habitants:

In [ ]:
df = df.sort_values('pop', ascending=False)
df.head()

### Retour sur le "piège des types"
Attention aux types des données quand Pandas lit un fichier csv.

In [ ]:
# Petit jeu de données d'exemple.
ex = pd.DataFrame({
    'genre': ['H', 'H', 'F', 'F'],
    'CSP': [1, 3, 2, 3],
    'revenu': ['15k', '50k', '25k', '30k']
})
ex

Ici on a une colonne `CSP` interprétée incorrectement comme numérique, et une colonne `revenu` interprétée incorrectement comme "objet".
Pour corriger ça:

In [ ]:
cats = ['genre', 'CSP']  # Colonnes catégorielles.
for col in cats:
    ex[col] = ex[col].astype('category')
    
# Pour revenu, c'est un peu plus délicat...
def transfo_revenu(revenu):
    """ Passe du format '10k' à 10000.
    Attention, le dernier caractère est simplement ignoré... """
    return 1000 * float(revenu[:-1])
    
ex['revenu'] = ex['revenu'].apply(transfo_revenu)
print(ex.dtypes)
ex

## Opérations numériques sur les colonnes

In [ ]:
# Nombre de lignes.
len(df)  # Ou df.shape[0] puisque df.shape est le tuple (nb de lignes, nb de colonnes).

In [ ]:
# Somme de la population des communes du tableau.
df['pop'].sum()

In [ ]:
# Produit (là ça plante, c'est trop gros...).
df['pop'].prod()

In [ ]:
# Maximum de la population des communes du tableau.
df['pop'].max()

In [ ]:
# Minimum de la population des communes du tableau.
df['pop'].min()

In [ ]:
# Moyenne de la population des communes du tableau.
df['pop'].mean()

In [ ]:
# Médiane de la population des communes du tableau.
df['pop'].median()

In [ ]:
# Variance de la population des communes du tableau.
print(np.var(df['pop']))  # Variance non corrigée.
print(df['pop'].var())    # Variance corrigée.

In [ ]:
# Matrices de covariances et de corrélations entre les colonnes numériques.
df.cov(numeric_only=True)
df.corr(numeric_only=True)

<div class="alert alert-info">
Ici on voit bien que les codes des villes, la variable STRATLOG, et les lattitudes et longitudes n'ont rien à faire ici.
Il faudrait alors sélectionner les colonnes qui nous intéressent pour donne une matrice de corrélation qui a du sens.
</div>

In [ ]:
col_num = ['pop', 'LOG', 'LOGVAC', 'surface']
df[col_num].corr()

In [ ]:
# Arrondi des valeurs (exemple pour obtenir les surfaces en km²)
(df['surface'] / 1e6).round(2)  # Argument = nombre de décimales.

In [ ]:
# Rangs des valeurs parmi l'échantillon
df['pop'].rank()  # Essayez avec l'argument `pct=True`.

## Filtrage de données

Rappelons que l'on travaille avec le tableau d'exemple obtenu par la
ligne

In [ ]:
df = pd.read_csv('rec99.csv', index_col=0)
df.columns = ['code', 'commune', 'BVQ_N', 'pop', 'LOG', 'LOGVAC', 'STRATLOG', 'surface', 'lat', 'lon']
df.head()

On l'a vu, la syntaxe `df[colonnes]` permet de récupérer une ou
plusieurs colonnes du tableau. Mais l'on peut aussi chercher à récupérer
des lignes précises.

Pour cela, la principale syntaxe utile est l'**utilisation de masques
booléens**. **En théorie**, un filtrage par masque booléen s'effectue
quand on passe une liste de booléen de longueur “nombre de lignes” à
l'intérieur de `df[...]`. Seules les lignes correspondantes à une valeur
`True` seront renvoyées. **En pratique** c'est très simple, ce que
l'on écrit ressemble à la syntaxe d'une phrase en français.

Exemple si l'on veut récupérer les lignes correspondant aux villes de plus de 5000 habitants:

In [ ]:
df[df['pop'] > 5000]  # Récupère les lignes du tableau correspondant à la condition "population > 5000".

Les **opérations booléennes ET, OU et NON**, au niveau des arrays/séries,
s'obtiennent au moyen des opérateurs `&`, `|` et `~`, ou bien (mais
c'est plus lourd à écrire), avec les fonctions `np.logical_and`,
`np.logical_or` et `np.logical_not`.

<div class="alert alert-info">
Attention à bien mettre des parenthèses autour de chaque "condition", sinon le code pourra fonctionner de manière inattendue.
</div>

**Exemples:**

In [ ]:
df[(df['pop'] > 5000) & (df['LOGVAC'] > 100)]

In [ ]:
df[(df['pop'] > 3*df['LOG']) | (df['surface'] < 1e6)]

Pour **combiner cette opération de filtrage par masques booléens avec
une sélection de colonnes**, on utilise la syntaxe
`df.loc[masque_lignes, colonnes]`. Ainsi, pour récupérer seulement
la latitude et longitude des communes de plus de 7000 habitants:

In [ ]:
df.loc[df['pop'] > 7000, ['lat', 'lon']]

Note: bien sûr, on peut ne passer qu'un seul nom de colonne: alors une
série est renvoyée.

**Indexation numérique**: on peut simplement vouloir récupérer les
lignes et colonnes données par leur position dans le tableau. On utilise
alors une syntaxe de slicing ou d'indexation par liste avec
`df.iloc[...]`.

In [ ]:
# Récupère les quatre premières lignes, avec les colonnes 3 et 1.
df.iloc[:4,[3,1]]

**Supprimer des lignes** identifiées par un masque booléen se fait
facilement avec les syntaxes vues ci-dessus: `df2 =
df[df['pop'] > 5000]` (on garde seulement les communes de plus de 5000 habitants).

## Graphiques

Le [tutoriel
de Seaborn](https://seaborn.pydata.org/tutorial.html) est assez clair,
je vais simplement donner quelques pistes, et les nombreux exemples en
lignes vous permettront en général de trouver comment faire ce que vous
cherchez à faire.

L'utilisation basique est la suivante:

-   (Optionnel) on charge le thème par défaut de Seaborn avec
    `sns.set_theme()`.
-   On utilise:
    -   `sns.relplot` pour des graphiques “relationnels” (tracer une
        variable en fonction d'une autre).
    -   `sns.displot` pour des graphiques “de distributions” (tracer
        un histogramme, une estimation de densité, etc.).
    -   `sns.catplot` pour des graphiques “catégoriels” (tracer de
        l'information suivant les catégories d'une variable).

-   Toutes les précisions sur comment doit se tracer le graphique sont
    déterminées par des arguments optionnels:
    -   L'argument optionnel (mais nécessaire) `data=df` précise le
        tableau utilisé pour produire le graphe.
    -   Si l'on doit mettre des variables en abscisses et en ordonnées:
        `x='var'` ou `y='var'`, ou `var` est le nom de la colonne
        dans `df`.
    -   Pour déterminer quelle sous-catégorie de graphique tracer:
        `kind='...'`. Les trois points sont à remplacer par
        -   pour `sns.relplot`: `'line'` pour avoir des courbes,
            `'scatter'` pour avoir un scatterplot,
        -   pour `sns.displot`: `'hist'` pour un histogramme,
            `'kde'` pour l'estimation de densité, etc.
        -   pour `sns.catplot`: `'bar'` pour un diagramme à barres,
            `'box'` pour des boîtes à moustache, etc.
    -   Pour distinguer différentes courbes ou points en changeant de
        couleur en fonction d'une variable catégorielle: `hue='var'`.
    -   Pour distinguer différentes courbes ou points en changeant de
        style (pointillés, ronds ou croix, etc.) en fonction d'une
        variable catégorielle: `style='var'`.
    -   Pour créer des sous-figures en fonction des valeurs d'une
        variable catégorielle:
        -   `row='var'` pour créer une ligne par valeur distincte de
            `var`.
        -   `col='var'` pour créer une colonne par valeur distincte de
            `var`.

In [ ]:
sns.set_theme()
# Exemple : on représente la population en fonction de la surface, pour toutes nos villes.
sns.relplot(df, x='LOG', y='pop', hue='surface')
plt.show()

In [ ]:
# Il existe de meilleurs manières de placer les villes sur une carte, mais ça nous donne une première idée.
sns.relplot(df, x='lat', y='lon', size='pop')
plt.show()

In [ ]:
sns.catplot(df, x='STRATLOG', y='LOGVAC', kind='box')
plt.show()

In [ ]:
# Bon, ce graphique n'est même pas forcément bien lisible, mais c'est pour montrer beaucoup de mots-clés différents.
sns.displot(df, x='pop', col='STRATLOG', stat="density", common_bins=False, kde=True, facet_kws=dict(sharex=False, sharey=False))
plt.show()

<div class="alert alert-info">
    On peut changer les nom des axes, et le titre de la    figure avec les commandes Matplotlib. Avec Seaborn, la légende est
mise automatiquement par défaut. Vous pouvez toujours utiliser
<code>plt.show()</code> pour afficher la figure (si le script est lancé dans
Spyder, la fenêtre graphique sera ouverte même sans <code>plt.show()</code>
mais ce n'est pas le cas en général).
</div>

**Exercice:** manipuler les graphiques précédents, rajouter des légendes, en créer d'autres...

Pour voir la syntaxe Seaborn en application dans plus d'exemples, allez
voir la [galerie](https://seaborn.pydata.org/examples/index.html) de
Seaborn. Il faudra s'en inspirer pour comprendre comment tracer vos
figures.

# Annexes et exercices

## Générer des nombres aléatoires avec Numpy

Le module Numpy fournit son générateur de nombres (pseudo-)aléatoires
avec le sous-module `np.random`. **Attention**: la bibliothèque
standard Python offre un module `random` aussi, mais celui-ci ne permet
pas de générer des objets Numpy. Donc dans un projet utilisant Numpy (et
dans tout ce cours), on n'utilisera **jamais le module** `random`
**standard**, mais bien le sous-module `np.random`, dont les
fonctionnements diffèrent. Soyez donc particulièrement vigilant, sur ce
sujet, à **chercher dans la bonne documentation**: celle de Numpy.

Grâce à `np.random`, il est possible de générer rapidement des `text` de
nombres aléatoires i.i.d. d'une certaine loi. La façon recommandée
d'opérer est la suivante:

1.  On définit au début du script un **générateur de nombres
    aléatoires** (*random number generator*) `rng` avec:

In [ ]:
rng = np.random.default_rng()

2.  On l'utilise pour générer ce que l'on veut:

In [ ]:
rng.uniform()  # Loi uniforme continue (entre 0 et 1 par défaut).

In [ ]:
rng.integers(10) # Variable uniforme sur un intervalle d'entiers.

In [ ]:
rng.binomial(100, 0.1)  # Variable binomiale.

In [ ]:
rng.poisson(17.4)  # Variable de Poisson.

In [ ]:
rng.normal(1, 5)  # Variables gaussiennes.

... et bien d'autres lois! Cf. [la
doc](https://numpy.org/doc/stable/reference/random/generator.html#numpy.random.Generator)
pour la liste complète.

Ce qui est important est que l'on peut générer très rapidement des vecteurs ou des tableaux de variables indépendantes, en utilisant l'argument optionnel `size`.

In [ ]:
rng.normal(size=(5, 3))  # Expérimentez avec cet argument.

**Important**: il est possible de *seeder* l'aléa de vos simulations en
donnant un argument à la fonction `rng =
np.random.default_rng(seed=0)`. Cet argument est appelé la *seed*
(graîne, ici donnée comme valant 0), et permet de reproduire les
simulations à l'identique (c'est le principe du pseudo-aléatoire). Sans
argument, le générateur est “auto-seedé”, et vos simulations ne seront
pas reproductibles à l'identique.

## Opérations avancées sur les séries, str, datetime

- Appliquer une **transformation "complexe"** sur une colonne. Avant de faire ça, vérifier s'il n'existe pas une solution déjà prévue par Pandas.

In [ ]:
# On se fixe un petit dataframe avec une série.
df0 = pd.DataFrame(df['pop'].head())
df0

In [ ]:
def racine(x):
    return np.sqrt(x)
df0['avec_apply'] = df['pop'].apply(racine)
df0['avec_numpy'] = np.sqrt(df['pop'])
df0  # Les deux lignes ci-dessus construisent des colonnes identiques.

- **Transformation sur les chaînes de caractères.**

In [ ]:
df0['commune'] = df['commune'].head().str.title()  # On change la capitalisation des noms des communes.
df0

Plus de détails sur les méthodes de type `a.str.fonction` peuvent être
trouvés sur [cette
page](https://pandas.pydata.org/docs/user_guide/text.html#string-methods)
de la documentation.

- Les séries dont les données sont de type `datetime` ont aussi leurs
    fonctions spécifiques, que l'on peut appeler avec `a.dt.fonction`.

**Exemple:**

In [ ]:
a = pd.to_datetime(pd.Series(['2019-02-12', '2020-11-28']))
df1 = pd.DataFrame({
    'série originale': a,
    'jour': a.dt.day,
    'mois': a.dt.month,
    'nom du mois': a.dt.month_name()
})
df1

Plus de détails en commençant par [cette
page](https://pandas.pydata.org/docs/getting_started/intro_tutorials/09_timeseries.html),
puis en cherchant toutes les fonctions de la forme `a.dt.fonction`
sur la page de l'objet
[`Series`](https://pandas.pydata.org/docs/reference/series.html).

- **Chercher si la valeur d'une colonne donnée est dans une liste.**

In [ ]:
noms = ["FENOUILLET", "BLAGNAC", "SAINT-JORY", "GAGNAC-SUR-G", "LESPINASSE"]
df[df['commune'].isin(noms)]

## Valeurs manquantes.

Ici, on ne va pas voir comment traiter les données manquantes pour des
problèmes complexes de statistique. La question est de savoir, étant
donnée une série `a`, quels sont les indices des lignes sans valeur.
Pour Pandas, une valeur manquante est un objet spécial (`np.nan` ou
`pd.NA`), représenté par `NaN` ou `<NA>`.

Les méthodes `a.isna()` et son “inverse” `a.notna()` permettent
d'obtenir un **masque booléen disant, pour chaque ligne, si la valeur
est manquante ou non**.

Pour un tableau `df`, le code `df = df.dropna()` **élimine les lignes
contenant une valeur manquante**.

Pour trouver d'autres informations sur le traitement de données manquantes avec Pandas, on redirige vers [la
documentation](https://pandas.pydata.org/docs/user_guide/missing_data.html#missing-data).

## Restructurer les données

- **Fusions** de tableaux avec les méthodes `df.join`, `df.merge` et `pd.concat`. Les deux premières
permettent d'opérer une **fusion en largeur** (joindre des colonnes), et
la dernière permet d'opérer une **fusion en longueur** des tableaux
(joindre des lignes).
- **Pivot** d'un tableau: méthode `df.pivot`. Usages spécifiques, on ne détaille pas ici.
- **Melting** d'un tableau: `df.melt`.

Pour la suite, on modifie le jeu de données `rec99` pour ajouter une nouvelle variable catégorielle.

In [ ]:
# On reprend la densité de population.
s = df['pop'] / df['surface'] * 1e6
df['densite'] = s
# On stratifie la densité
df['strat_densite'] = pd.cut(df['densite'], [0, s.median(), s.mean(), np.inf], labels=['low', 'med', 'high'])
sns.catplot(df, x='strat_densite', y='pop')
plt.show()

### Agrégation

Pour effectuer une opération sur les différentes valeurs d'une colonne catégorielle:

In [ ]:
# Moyenne de la population, des logements et de la surface des villes de densités spécifiées.
df.groupby('strat_densite')[['pop', 'LOG', 'surface']].mean()

On peut complexifier l'agrégation pour obtenir plusieurs calculs en même temps:

In [ ]:
# Syntaxe un peu différente, via `agg` et un dictionnaire.
df.groupby('strat_densite').agg({'pop': ['median', 'mean', 'std'], 'LOG': ['median', 'max'], 'surface': 'mean'})

#### Fenêtres roulantes.

Un autre type d'agrégation est l'agrégation par fenêtres roulantes en
utilisant `df.rolling`. On considère le tableau suivant:

In [ ]:
df2 = pd.DataFrame(np.arange(12).reshape((6,2)), columns=['A','B'])
df2

In [ ]:
# Moyenne des valeurs, le long de chaque colonne, sur une fenêtre de 3 lignes
df2.rolling(3).mean()

In [ ]:
# Comme pour `groupby`, on peut utiliser plusieurs fonctions d'agrégation:
df2.rolling(3).agg(['min', 'sum'])

In [ ]:
# Pour centrer la fenêtre roulante.
df2.rolling(3, center=True).mean()

- **Cas des dates**.

In [ ]:
# On fait en sorte que l'index soit de type "date".
df2.index = pd.to_datetime(['2022-11-01', '2022-11-02', '2022-11-04', '2022-11-05', '2022-11-08', '2022-11-10'])
df2

In [ ]:
df2.rolling('3d').sum()

Noter que la durée prise en compte par défaut est par défaut la durée
qui précède la date de la ligne. Pour centrer autour de la date de la
ligne, on utilise à nouveau l'argument optionnel `center=True`. Enfin,
l'argument `'3d'` désigne trois jours, mais on peut aussi écrire
`'3m'` pour trois minutes, `'3s'` pour trois secondes, etc. Toute
chaîne qui est acceptée par le constructeur `pd.Timedelta` (objet qui
contient un différentiel de temps) est acceptée par cette fonction
`df.rolling`.

## Exercices

**Exercice :** Sur [cette
page](https://statistique.quebec.ca/fr/document/noms-de-famille-au-quebec/tableau/estimation-de-leffectif-des-1-000-premiers-noms-de-famille-par-ordre-alphabetique-quebec-2005)
du site `statistique.quebec.ca` se trouve une estimation de l'effectif
des 1000 noms de familles les plus courants au Québec, dans un tableau
HTML. Le but de cet exercice est d'importer ce tableau avec Pandas, de
manière utilisable. Évidemment, il n'y a pas de fichier `csv` fourni sur
le site, sinon ce serait trop simple!

1.  Effectuer la requête `tables = pd.read_html(url)`, où `url` est
    une chaîne de caractère contenant l'URL de la page qui nous
    intéresse.  
    *Il est possible que vous ayez besoin d'installer le module* `lxml`
    *avec Anaconda, puis de redémarrer Spyder pour que cette commande
    fonctionne.*
2.  Que récupère-t-on dans la variable tables? Récupérer le dataframe
    qui nous intéresse dans une variable `df`, puis exporter-le dès à
    présent dans un fichier `brut.csv`.  
    *Maintenant, vous pouvez commenter tout le début de votre script (en
    particulier l'appel à* `pd.read_html`*) et le remplacer par* `df =
    pd.read_csv('brut.csv')`.
3.  Afficher les premières lignes de `df` et ses dernières lignes.
    Effacer celles qui sont sans intérêt.
4.  Séparer le tableau judicieusement en quatre tableaux dans le sens de
    la largeur.
5.  Pour chacun de ces tableaux, supprimer la colonne inutile et
    renommer les autres en `'rang'`, `'nom'` et `'nombre'`.
6.  Empiler les quatre tableaux en un seul en utilisant `pd.concat`.
    Assigner le tableau résultant à la variable `df`.
7.  Si tout va bien, votre tableau a 1000 lignes et 3 colonnes. Si ce
    n'est pas le cas, réparer le script jusqu'à obtenir ce que l'on
    veut. Enfin, exporter le tableau dans un fichier `noms0.csv`.

**Exercice :** On reprend l'exercice précédent (on suppose donc
l'existence du fichier `noms0.csv` comme obtenu à la fin de l'exercice).

1.  On voudrait classer le tableau par ordre de rang croissant, plutôt
    que par ordre alphabétique. Afficher les premières lignes de
    `df.sort_values('rang')`. Quel est le souci ?
2.  On voudrait donc convertir les types des colonnes `rang` et `nombre`
    en `int`. Quel autre problème rencontre-t-on, si l'on essaie la
    méthode la plus directe?
3.  Écrire une fonction `asint(text)` qui enlève les espaces de la
    chaîne de caractère `text` puis utilise `int()` pour renvoyer
    l'entier correspondant.  
    *Pour enlever les espaces, on pourra penser par exemple aux
    fonctions* `split` *et* `join`*, ou au module* `re`.
4.  Grâce à la question précédente, changer les deux colonnes
    problématiques de `df` en colonnes d'entiers, puis trier le tableau
    par ordre croissant de `rang` et le ré-indexer.
5.  Quels sont les 35 noms les plus courants au Québec? Votre nom
    fait-il partie de la liste des 1000?
6.  (Optionnel) Enregistrer le tableau dans un fichier `noms.csv` pour
    pouvoir l'admirer plus tard.

Le site <a href="data.gouv.fr" class="uri">data.gouv.fr</a> vise à
rassembler de nombreux jeux de données concernant la France: si vous
cherchez des données pour un projet, vous pouvez notamment chercher
là-dedans (ou dans le site *our world in data*, dont on parle plus bas).
L'exercice suivant propose de travailler avec un jeu de données de
enregistré sur ce site.

**Exercice :** Dans cet exercice, on s'intéressera aux températures
quotidiennes par département.

1.  Importer les
    [données](https://www.data.gouv.fr/fr/datasets/r/dd0df06a-85f2-4621-8b8b-5a3fe195bcd7)
    dans un tableau `temp`. Changer la colonne `date_obs` en type
    “`datetime`”.
2.  Se fixer une liste de trois départements et restreindre le jeu de
    données à ceux-ci.
3.  Tracer les courbes de températures moyennes au cours du temps, pour
    vos départements. Qu'est-ce qui gène la lisibilité?
4.  On voudrait utiliser Pandas pour lisser les données sur une fenêtre
    roulante. Écrire une fonction `lissage(df, colonne, methode,
    fenetre)` qui:
    -   Pivote `df` pour avoir les dates en index, les départements en
        colonne et la colonne initiale `colonne` en valeurs.
    -   Utilise `rolling` puis `agg` pour faire l'opération décrite par
        `methode`, sur une fenêtre donnée par `fenetre`.
    -   Utilise `melt` pour remettre les données en forme avec les trois
        colonnes `date_obs`, `departement` et “`colonne`” (avec son nom
        initial.
        Le tableau modifié par ces opérations successives est finalement
        renvoyé.
    Concrètement, on doit pouvoir utiliser `df = lissage(temp, 'tmoy',
    'mean', '60d')` pour obtenir les données moyennées sur une fenêtre
    de 60 jours.  
    Note: *On pourrait lisser les données de minimum, moyenne et maximum
    en même temps mais ça reste complexe. Exo bonus: chercher à faire
    cela en ne manipulant qu'un seul tableau.*
5.  Utiliser la fonction précédente pour tracer le graphe des
    températures maximales, puis le graphe des températures moyennes,
    sur une fenêtre roulante de 60 jours, pour les départements
    considérés.
6.  On veut tracer le profil de température d'une année typique, pour
    chaque département. Pour cela:
    -   Ajouter une colonne `semaine` au tableau, qui contient le numéro
        de la semaine dans l'année (de 1 à 52). *On pourra utiliser la
        méthode* `pandas.Series.dt.isocalendar`.
    -   Ajouter une colonne année, de manière similaire.
    -   En utilisant la méthode `temp.groupby`, puis la méthode `agg`,
        définir un nouveau tableau `temp_groupe` dont chaque ligne
        correspond à un département, une année et une semaine, et dont
        les colonnes `tmin` et `tmax` sont définies comme les minimums
        et maximums des températures observées sur la semaine en
        question.
7.  Afficher les profils de vos départements avec
    ```python
    sns.relplot(data=temp_groupe, x='tmin', y='tmax', hue='departement')
    ```

Le 15 novembre 2022, la population mondiale a atteint **8 milliards
d'êtres humains**, alors que vous vous rappelez peut-être avoir appris
enfant que l'on était 6 milliards (c'était le cas autour de l'an 1999).
Les deux exercices suivants ont pour but de “fêter” cet événement et de
nous permettre de (re)visualiser la croissance de la population humaine
au cours de son histoire.

**Exercice :** Sur [cette
page](https://ourworldindata.org/grapher/population) du site [our world
in data (OWID)](https://ourworldindata.org/), vous trouverez un graphe
interactif montrant l'évolution de la population dans différentes
régions du monde, depuis l'an -10 000. Les données utilisées sur ce
graphe proviennent de plusieurs sources: on peut cliquer sur l'onglet du
graphe “Sources” pour les voir, (on pourrait donc télécharger les
données brutes et faire une analyse détaillée). Dans cet exercice, on va
directement télécharger les données agrégées et nettoyées par les
scientifiques de OWID.

1.  Cliquer sur l'onglet “Download” et télécharger le fichier CSV
    proposé. Mettez-le dans le même dossier que votre script.
2.  Utiliser Pandas pour charger le jeu de données dans un tableau
    `dfpop1`.
3.  Explorer le tableau avec Pandas: afficher le nom des colonnes, leurs
    types.  
    *Si vous trouvez que des colonnes ont un nom trop long, vous pouvez
    les renommer.*
4.  Utiliser Seaborn pour tracer l'évolution de la population mondiale
    (attention, on parle de tracer une seule courbe) au cours du temps.
5.  On voudrait maintenant comparer l'évolution de la population de nos
    pays préférés au cours du temps.  
    Écrire une fonction `regions_par_pop(df, annee)` qui renvoie un
    tableau dont les lignes sont les pays et l'unique colonne donne le
    nombre d'habitants pour l'année passée en argument. L'argument `df`
    est bien sûr censé recevoir la variable `dfpop1`.
6.  En ordonnant les régions du monde par nombre d'habitants en l'an
    2000, identifier votre pays favori et trois autres pays qui ont un
    nombre d'habitants comparable. Enregistrer leurs noms dans une
    liste.
7.  Écrire une fonction `plot_pays(df, liste_pays, depart=None)` qui
    trace sur un même graphe l'évolution des populations des pays
    listés, depuis l'année `depart` (dans le cas `depart=None`, ne pas
    mettre de restriction d'années).  
    Tester sur vos pays favoris. Améliorer l'affichage si nécessaire.

**Exercice :** Cet exercice fait la paire avec l'exercice précédent: sur
[cette
page](https://ourworldindata.org/grapher/population-growth-the-annual-change-of-the-population)
se trouve un graphe qui montre le taux de croissance (en naissance / an)
de différentes régions du monde, avec des projections jusqu'à l'an 2100.
Encore une fois vous trouverez la source: ce sont les prévisions de
l'ONU.

1.  Utiliser l'onglet “Download” pour télécharger les données au format
    CSV, et les importer dans un tableau `dfpop2`.
2.  Remarquons que les prédictions et les données connues (plus
    exactement les estimations du passé) sont dans deux colonnes
    différentes. On va changer ça:
    -   Rajouter au tableau une colonne `'Prédiction'` de valeurs
        booléennes, qui indique si la ligne correspond à une prédiction
        ou non.
    -   Réunir les deux colonnes des taux de croissances dans une seule
        colonne appelée `'Croissance'`. Les deux anciennes colonnes
        seront supprimées.
3.  Sur la même figure, tracer les deux courbes du taux de croissance
    mondial (réel pour les années 1951–2021 et prédit pour les années
    2022–2100). Faire en sorte que les deux courbes s'affichent avec la
    même couleur, la deuxième en pointillés.
4.  On veut maintenant prédire les populations des différents pays pour
    les années 2021–2100.  
    Grâce à la méthode `dfpop2.pivot`, construire un tableau
    `dfpop2_pivot` ayant pour lignes les années, pour colonnes les
    régions et pour valeurs les taux de croissance par année.
5.  Construire similairement `dfpop1_pivot` à partir du tableau `dfpop1`
    de l'exercice précédent.
6.  Construire un tableau `dfpop3` de la manière suivante:
    -   Utiliser la fonction `pd.concat` pour construire la
        concaténation de la ligne de `dfpop1_pivot` correspondant à
        l'année 2021 avec les lignes de taux de croissance prédit (donc
        à partir de 2022) du tableau `dfpop2.pivot`. On pourra ignorer
        les colonnes non présentes dans les deux tableaux grâce à
        l'argument optionnel `join='inner'`.
    -   Effectuer la somme cumulée le long des colonnes pour obtenir les
        prévisions pour les années 2022–2100.
7.  Enfin, modifier `dfpop3` pour intégrer les lignes correspondant aux
    années passées (normalement, elles sont dans `dfpop1_pivot`).
8.  Modifier la fonction `plot_pays(df, liste_pays, depart=None)` de
    l'exercice précédent pour qu'elle intègre les prévisions, affichées
    en style “tirets”. Cette fois, l'argument `df` sera destiné à
    recevoir la variable `dfpop3`.  
    Tester sur vos pays favoris. Améliorer l'affichage si nécessaire.

**Exercice :** Reproduire du mieux possible les graphiques des pages
suivantes:

-   [Performance scolaire des enfants de 15
    ans](https://ourworldindata.org/grapher/pisa-scores-of-15-year-olds-by-reading-proficiency-level).

-   [Genre des
    fumeurs](https://ourworldindata.org/grapher/comparing-the-share-of-men-and-women-who-are-smoking).

-   [Morts dues à la pollution de
    l'air](https://ourworldindata.org/grapher/death-rate-from-pm25-vs-pm25-concentration).

-   [Part des véhicules électriques et
    hybrides](https://ourworldindata.org/grapher/battery-plugin-hybrid-vehicles).

-   [Consommation de viande par
    personne](https://ourworldindata.org/grapher/meat-supply-per-person?tab=chart).

-   [Démocraties et
    dictatures](https://ourworldindata.org/grapher/people-living-in-democracies-autocracies).

**Exercice :** Trouvez vos propres jeux de données à manipuler avec
Pandas et Seaborn sur [`data.gouv.fr`](https://www.data.gouv.fr), [our
world in data](https://ourworldindata.org) ou un autre site de votre
choix.